# Hyperparameter Optimization & Neural Architecture Search

In [1]:
# Import the necessary modules
import os
# Surpress unnecessary output from tensorflow package
os.environ['TF_CPP_MIN_LOG_LEVEL'] = '3'
# Suppress unnecessary output from ray package
os.environ['RAY_DEDUP_LOGS'] = '0'

# Import necessary functions
from PINNLearning.training import learning_rate_schedule, oneD_loss
from PINNLearning.data import gen_data, set_boundaries, add_noise
from PINNLearning.models import create_model

# Import packages for HPO
from ray import tune
from ray.tune.search.bohb import TuneBOHB
from ray.tune.search import ConcurrencyLimiter
from ray.tune.schedulers.hb_bohb import HyperBandForBOHB
from ray.tune.schedulers import HyperBandScheduler
from ray.tune.search.optuna import OptunaSearch
import tensorflow as tf
import keras

As can be seen throughout this series of notebooks, there are many parameters that must be set prior to the actual training of the neural network. Such parameters are called hyperparameters. In some cases, they can significantly influence the performance of the learning algorithm and, thus, the final network.


For example, a **learning rate schedule** is created to reduce the size of the steps the optimization algorithm takes during the learning phase. This helps the algorithm converge to the optimal solution more easily and quickly by preventing it from missing the solution. However, this raises questions about how the numerical values of the schedule should be set: _Should there be a larger initial learning rate? After how many epochs should the first reduction occur? By how much should it be reduced?_


These are all questions typically answered by domain or machine learning experts, but they still remain educated guesses. Thus, in many cases – depending on the complexity of the problem – it can be a good decision to search for the most optimal **configuration (set) of hyperparameters** before actually beginning the training of the neural network. Algorithms that complete this task are numerous and of high interest to modern research; such problems are called **hyperparameter optimization (HPO)**.


A special type of hyperparameter is the **neural network architecture** itself. It raises questions like: _How many layers should it have? How many weights should each layer possess? And for more complex models (like CNNs), which type of layer should be used?_
The importance of these "parameters" cannot be understated, as they mark the difference between the model's ability to converge to the proper solution or not.


According to the law of general convergence, any function can be approximated if the neural network is sufficiently large. For simpler problems with ample data, like those present across these notebooks, the dimensions can be typically set to relatively large values and will thus converge comfortably.
As such, for most data sets NAS is in fact **not** necessary to reach comparable results to the optimal solution.
However, as networks increase in size and the tasks become more complex, this approach reaches its (resource) limitations and needs to be solved algorithmically, similar to the other hyperparameters.


Although the grave importance of these parameters is well known, the process of **neural architecture search (NAS)** has yet to receive the same scientific attention.
For all intended purposes, in the case of "simpler" and smaller network structures (those that can be easily defined with a few individual parameters, such as in **cell structures** or **sequential/chain structures**), it is often sufficient to incorporate these parameters into the existing hyperparameter optimization frameworks. 
However, for highly complex structures with a numerous parameters, it can be more efficient to implement specialized optimization algorithms (see e.g.: [One-Shot Model](https://arxiv.org/abs/1911.11090)).

Additional in depth information on HPO: [Book](https://arxiv.org/abs/2410.22854v2)

Addtitional information and literature on NAS: [Information](https://theaisummer.com/neural-architecture-search/), [Literature](https://www.automl.org/nas-overview/)

In [2]:
# Setting the boundary conditions
x_bc, y_bc = set_boundaries([[0.0], [1.0]], [[1.0], [0.0]])

# Create some training and validation data
x_train = gen_data(0.0, 1.0, 100)
x_val = tf.reshape(add_noise(x_train, 0.2, end_values=False, bounds=[0.0, 1.0]), [-1])
x_val, idx = tf.unique(x_val)
x_val = tf.expand_dims(x_val, axis=1)  # Get train and val values for proper evaluation

# Pad the bc values and concatenate everthing needed for the loss function into 1 tensor
# as the keras trainer expects the input in the form of: (x_train, y_train)
x_bc_padded = tf.pad(x_bc, tf.constant([[0, len(x_train) - 2], [0, 0]]))
y_bc_padded = tf.pad(y_bc, tf.constant([[0, len(x_train) - 2], [0, 0]]))
x_bc_padded2 = tf.pad(x_bc, tf.constant([[0, len(x_val) - 2], [0, 0]]))
y_bc_padded2 = tf.pad(y_bc, tf.constant([[0, len(x_val) - 2], [0, 0]]))
y_train = tf.concat([x_train, x_bc_padded, y_bc_padded], axis=1)
y_val = tf.concat([x_val, x_bc_padded2, y_bc_padded2], axis=1)

There are many different packages available for solving **HPO** problems, each with specific advantages and disadvantages. Often, there are dedicated packages for individual optimization methods.
One of the most popular options is [Ray](https://docs.ray.io/en/latest/tune/index.html) (also known as Ray Tune), which provides a framework to integrate various optimizer packages in a consistent manner. This allows for a wide range of methods to be utilized effectively.
Ray Tune also supports automatic scaling and parallelization across multiple CPUs and/or GPUs, whether on a local machine or a server cluster.

**ATTENTION: Execute the following code with caution, as it will fully utilize all available CPUs if no GPU is present, potentially blocking the computer!**

To limit the number of parallel instances, use the line: _algo = ConcurrencyLimiter(algo, max_concurrent=n)_, where n should be less than or equal to the number of CPU cores. However, be aware that this may increase the overall runtime.

****

Every **HPO** algorithm is based on three key definitions:
- Definition of the Search Space
- Definition of the Evaluation Function
- Definition of the Tuner


**Search Space**

The search space describes a high-dimensional space created by the hyperparameters that need to be optimized. This results in a _hybrid space_ where continuous and discrete dimensions are mixed. Any point in this space represents a single **configuration** of hyperparameters and corresponds to a certain return through the evaluation function.
The definition of this space varies between packages; some incorporate it within the evaluation function, while others define it explicitly. However, the process remains consistent: assign a name to each parameter and set the corresponding value to the sampling of the tuner within a specified range (either discrete from a list or from a continuous distribution).

In some cases, the dimensions of the space may change during the optimization process, depending on the values of certain parameters. For example, as the number of layers increases, the number of parameters required to describe the weights per layer also changes. However, most algorithms rely on a _static feature space_. Therefore, it is advisable to **instantiate the maximum possible parameters and truncate** the optimal configuration to the necessary parameters.


**Evaluation Function**

This function first _creates a model_ with all the settings that would be applied to the final neural network to **approximate** its performance. It then trains and evaluates the model, with the output commonly being used by the tuner to inform the optimization process.
Each call to this function is called a **"trial"**.

An important consideration is the **number of epochs** for which the model is trained. The larger this value (and thus closer to the value needed for full convergence), the longer it takes to evaluate each individual configuration. However, this also _improves the approximation_ of the final network's performance. If the training phase of the final network is time-limited (where time is measured in epochs), this parameter should be included as another one to be optimized.


**Tuner**

The tuner takes the _search space_ and the _evaluation function_ to set up the optimization algorithm, making adjustments and configurations as needed.

In Ray Tune, there is a distinction between the **search algorithm** and the **scheduler**. The **search algorithm** defines how hyperparameter configurations are sampled from the _search space_, with the default method being simple random sampling. The **scheduler** manages the configurations throughout the optimization process, such as stopping the run early if the model's improvement is too slow. By default, no scheduler is set.

If neither is provided, a certain number of samples is taken and fully evaluated, with the best-performing configuration being returned.

In [3]:
# Description of all hyper parameters that need to be searched
search_space = {
    "epochs": 600,                                                     # training parameter for the evaluation model --> convergence of model expected at 1500-2000 
    "init_lr": tune.choice([i/10000 for i in range(5, 50)]),           # FLOAT: min_value=0.5e-3, max_value=5e-3, step=0.1e-3
    "reduct_steps_lr": tune.choice(list(range(100, 2000))),            # INT: min_value=100, max_value=2000
    "reduct_rate_lr": tune.choice([i/100 for i in range(10, 99, 1)]),  # FLOAT: min_value=0.1, max_value=0.99, step=0.01
    "l2_penalty": tune.choice([i/1000 for i in range(5, 500)]),        # FLOAT: min_value=0.005, max_value=0.5, step=1e-3
    "num_layers": tune.choice(list(range(2, 10)))                      # INT: min_value=2, max_value=10
}
# Adding the weights per layer for all possible layers
search_space.update(
    {f"num_weights_layer_{i + 1}": tune.choice(list(range(2, 50))) for i, _ in enumerate(range(11))}  # INT: min_value=2, max_value=50 for each num_layers
)

In [4]:
# Describing, training and evaluating the model to get best HP performance
def train_model(hp):
    # defining the learning rate schedule with its searchable parameters
    lr_schedule = learning_rate_schedule(
        hp["init_lr"],
        hp["reduct_steps_lr"],
        hp["reduct_rate_lr"]
    )

    # creating the model with searchable regularizer, #layers and #weights per layer
    weigts = []
    for i in range(hp["num_layers"]):
        weigts.append(hp[f'num_weights_layer_{i + 1}'])
    model = create_model(hp["num_layers"], weigts, l2=hp["l2_penalty"])

    # closure function to convert the expected keras training function loss format
    # (y_true, y_pred) to the implemented custom loss function 
    def custom_loss(y_true, y_pred):
        x_train = y_true[:, 0]
        xbc = y_true[:, 1][0:2]
        ybc = y_true[:, 2][0:2]
        return oneD_loss(model, x_train, xbc, ybc)

    # finish the model by assigning the optimizer and the loss
    model.compile(
        optimizer=keras.optimizers.Adam(
            learning_rate=lr_schedule),
        loss=custom_loss
    )

    # unlike in the other notebooks use keras build-in trainer
    history = model.fit(
        x_train, y_train,
        validation_data=(x_val, y_val),
        epochs=hp["epochs"],
        batch_size=32,
        verbose="0"
    )
    # get the final validation loss
    val_loss = history.history['val_loss'][-1]
    # report results to the tuner
    tune.report({"loss": val_loss})

## Bayesian Optimization (BO)

There are multiple ways to construct a search algorithm, one of which is the model-based approach.


In this context, it is important to understand that the _evaluations_ of tested hyperparameter configurations represent _observations_ (points) of an objective function (e.g., the loss) across the search space.
The goal is to **minimize** this function to find the optimal configuration. To achieve this, the objective function is approximated using a **surrogate model**. In the case of **BO**, this model is probabilistic, providing predictions along with their likelihoods. While many models (including non-probabilistic ones) are possible, the most common choice is **Gaussian Processes (GPs)**.


The working process generally follows the diagram below (source: [Link](https://medium.com/data-science/shallow-understanding-on-bayesian-optimization-324b6c1f7083) [accessed 13 Jun 2025]). In this diagram, the striped line represents the _real_ objective function, which is typically unknown. The solid line demonstrates the _current mean_ of the model across the search space, with the shaded area indicating the _uncertainty_ of the values at the respective points.


Each graph represents one iteration of the algorithm. It begins with a prior probability distribution, which is updated to a posterior distribution in each iteration by evaluating a hyperparameter configuration and using the resulting observation to train the surrogate model. At these observed points, the uncertainty decreases while also reducing in the surrounding area.
The sampling of the next point is based on the _maximization_ of the heuristic **acquisition function**. This function utilizes the mean and variance from the previous iteration to typically calculate either the **Expected Improvement (EI)**, the **Probability of Improvement (PI)**, or the **Upper Confidence Bound (UCB)**. The goal is to strike a good balance between exploitation (refining known good configurations) and exploration (searching new areas of the hyperparameter space) of the (un)known search space.


For more information on these topics, see: [Wikipedia](https://en.wikipedia.org/wiki/Bayesian_optimization).


<img src="./data/images/BO demonstration.webp" alt="Depiction of the BO process" style="width:500px;"/>



Bayesian Optimization is highly regarded for its efficiency in optimizing functions where the _evaluations are costly_. Its ability to model uncertainty and make informed decisions about where to sample next in the hyperparameter space allows it to require fewer evaluations to find optimal hyperparameters. This makes it particularly suitable for high-dimensional and complex search spaces, which are common in fields such as computer vision, natural language processing, and reinforcement learning.
Furthermore, it is guaranteed to **converge to an optimal configuration** (though this could also be a _local minimum_) of hyperparameters if given enough iterations.
However, in cases where the evaluation is not costly, the overhead from learning the surrogate model may outweigh the benefits of this method.
Furthermore, this method is also very sensetive to its own hyperparameters.

The package used here for **BO** is called Optuna. It is an open-source hyperparameter optimization framework designed to automate the process of tuning machine learning models and includes various optimization algorithms.

Optuna implements **Bayesian optimization** by replacing the **Gaussian Processes (GPs)** with a technique called the **Tree-structured Parzen Estimator (TPE)**. **TPE** is a probabilistic model that estimates the distribution of good and bad hyperparameter configurations based on past evaluations.
The **TPE** approach allows Optuna to effectively balance _exploration_ and _exploitation_.
For more information on **TPE**, refer to the original paper [here](https://arxiv.org/abs/2304.11127).

In combination with Ray Tune, this framework allows for running multiple **trials** in parallel, which is a deviation from the classic approach but only affects the implementation and not the underlying method itself. This parallelization can significantly speed up the hyperparameter optimization process, making it more efficient in practice.

In [ ]:
# Defining the tuner as Bayesian Optimization following the implementation
# of the Optuna package

# defintion of the search algorithm
algo = OptunaSearch()  # optuna defaults to TPESampler
# get absolute output path
output_dir = os.path.abspath("./data/HPO_results")

# definition of the tuner
tuner_BO = tune.Tuner(
    trainable=train_model,
    param_space=search_space,
    tune_config=tune.TuneConfig(
        metric="loss",             # which metric to evaluate
        mode="min",                # minimize or maximize the metric
        search_alg=algo,           # set the HP Optimizer
        num_samples=50             # number of iterations
    ),
    run_config=tune.RunConfig(
        storage_path=output_dir, name="BO",
        verbose=1
    )
)

# complete the tuning process
results = tuner_BO.fit()

(train_model pid=67883) Epoch 1/600


(train_model pid=67883) WARNING:tensorflow:Calling GradientTape.gradient on a persistent tape inside its context is significantly less efficient than calling it outside the context (it causes the gradient ops to be recorded on the tape, leading to increased CPU and memory usage). Only call GradientTape.gradient inside the context if you actually want to trace the gradient in order to compute higher order derivatives.


(train_model pid=67883) Epoch 2/600
(train_model pid=67883) Epoch 3/600
(train_model pid=67883) Epoch 4/600
(train_model pid=67883) Epoch 5/600
(train_model pid=67883) Epoch 6/600
(train_model pid=67883) Epoch 7/600
(train_model pid=67883) Epoch 8/600
(train_model pid=67883) Epoch 9/600
(train_model pid=67883) Epoch 10/600
(train_model pid=67883) Epoch 11/600
(train_model pid=67883) Epoch 12/600
(train_model pid=67883) Epoch 13/600
(train_model pid=67883) Epoch 14/600
(train_model pid=67883) Epoch 15/600
(train_model pid=67883) Epoch 16/600
(train_model pid=67883) Epoch 17/600
(train_model pid=67883) Epoch 18/600
(train_model pid=67883) Epoch 19/600
(train_model pid=67883) Epoch 20/600
(train_model pid=67883) Epoch 21/600
(train_model pid=67883) Epoch 22/600
(train_model pid=67883) Epoch 23/600
(train_model pid=67883) Epoch 24/600
(train_model pid=67883) Epoch 25/600
(train_model pid=67883) Epoch 26/600
(train_model pid=67883) Epoch 27/600
(train_model pid=67883) Epoch 28/600
(train_mo

(train_model pid=67950) WARNING:tensorflow:Calling GradientTape.gradient on a persistent tape inside its context is significantly less efficient than calling it outside the context (it causes the gradient ops to be recorded on the tape, leading to increased CPU and memory usage). Only call GradientTape.gradient inside the context if you actually want to trace the gradient in order to compute higher order derivatives.


(train_model pid=67883) Epoch 86/600
(train_model pid=67883) Epoch 87/600
(train_model pid=67883) Epoch 88/600
(train_model pid=67883) Epoch 89/600
(train_model pid=67883) Epoch 90/600
(train_model pid=67883) Epoch 91/600
(train_model pid=67883) Epoch 92/600
(train_model pid=67883) Epoch 93/600
(train_model pid=67883) Epoch 94/600
(train_model pid=67883) Epoch 95/600
(train_model pid=67883) Epoch 96/600
(train_model pid=67883) Epoch 97/600
(train_model pid=67883) Epoch 98/600
(train_model pid=67883) Epoch 99/600
(train_model pid=67883) Epoch 100/600
(train_model pid=67883) Epoch 101/600
(train_model pid=67883) Epoch 102/600
(train_model pid=67883) Epoch 103/600
(train_model pid=67883) Epoch 104/600
(train_model pid=67883) Epoch 105/600
(train_model pid=67883) Epoch 106/600
(train_model pid=67883) Epoch 107/600
(train_model pid=67883) Epoch 108/600
(train_model pid=67883) Epoch 109/600
(train_model pid=67883) Epoch 110/600
(train_model pid=67883) Epoch 111/600
(train_model pid=67883) Ep

...

(train_model pid=87446) Epoch 185/600
(train_model pid=86968) Epoch 481/600
(train_model pid=87114) Epoch 400/600
(train_model pid=87597) Epoch 53/600
(train_model pid=86796) Epoch 587/600
(train_model pid=86968) Epoch 482/600
(train_model pid=87114) Epoch 401/600
(train_model pid=87279) Epoch 262/600
(train_model pid=87446) Epoch 186/600
(train_model pid=86796) Epoch 588/600
(train_model pid=87279) Epoch 263/600
(train_model pid=87446) Epoch 187/600
(train_model pid=87597) Epoch 54/600
(train_model pid=86968) Epoch 483/600
(train_model pid=87114) Epoch 402/600
(train_model pid=86796) Epoch 589/600
(train_model pid=87279) Epoch 264/600
(train_model pid=87446) Epoch 188/600
(train_model pid=87597) Epoch 55/600
(train_model pid=86796) Epoch 590/600
(train_model pid=86968) Epoch 484/600
(train_model pid=87114) Epoch 403/600
(train_model pid=87279) Epoch 265/600
(train_model pid=87446) Epoch 189/600
(train_model pid=87597) Epoch 56/600
(train_model pid=86968) Epoch 485/600
(train_model pid

(train_model pid=87894) WARNING:tensorflow:Calling GradientTape.gradient on a persistent tape inside its context is significantly less efficient than calling it outside the context (it causes the gradient ops to be recorded on the tape, leading to increased CPU and memory usage). Only call GradientTape.gradient inside the context if you actually want to trace the gradient in order to compute higher order derivatives.


(train_model pid=86968) Epoch 584/600
(train_model pid=87279) Epoch 362/600
(train_model pid=87114) Epoch 504/600
(train_model pid=87446) Epoch 289/600
(train_model pid=87597) Epoch 153/600
(train_model pid=87755) Epoch 62/600
(train_model pid=86968) Epoch 585/600
(train_model pid=87279) Epoch 363/600
(train_model pid=87114) Epoch 505/600
(train_model pid=87446) Epoch 290/600
(train_model pid=87597) Epoch 154/600
(train_model pid=87279) Epoch 364/600
(train_model pid=87755) Epoch 63/600
(train_model pid=86968) Epoch 586/600
(train_model pid=87597) Epoch 155/600
(train_model pid=87114) Epoch 506/600
(train_model pid=87446) Epoch 291/600
(train_model pid=87755) Epoch 64/600
(train_model pid=87279) Epoch 365/600
(train_model pid=86968) Epoch 587/600
(train_model pid=87114) Epoch 507/600
(train_model pid=87446) Epoch 292/600
(train_model pid=87597) Epoch 156/600
(train_model pid=87755) Epoch 65/600
(train_model pid=86968) Epoch 588/600
(train_model pid=87279) Epoch 366/600
(train_model pid

(train_model pid=88015) WARNING:tensorflow:Calling GradientTape.gradient on a persistent tape inside its context is significantly less efficient than calling it outside the context (it causes the gradient ops to be recorded on the tape, leading to increased CPU and memory usage). Only call GradientTape.gradient inside the context if you actually want to trace the gradient in order to compute higher order derivatives.


(train_model pid=87446) Epoch 393/600
(train_model pid=87597) Epoch 253/600
(train_model pid=87755) Epoch 163/600
(train_model pid=87894) Epoch 51/600
(train_model pid=87279) Epoch 464/600
(train_model pid=87446) Epoch 394/600
(train_model pid=87597) Epoch 254/600
(train_model pid=87755) Epoch 164/600
(train_model pid=87894) Epoch 52/600
(train_model pid=87279) Epoch 465/600
(train_model pid=87446) Epoch 395/600
(train_model pid=87597) Epoch 255/600
(train_model pid=87755) Epoch 165/600
(train_model pid=87279) Epoch 466/600
(train_model pid=87597) Epoch 256/600
(train_model pid=87755) Epoch 166/600
(train_model pid=87894) Epoch 53/600
(train_model pid=87279) Epoch 467/600
(train_model pid=87446) Epoch 396/600
(train_model pid=87894) Epoch 54/600
(train_model pid=87446) Epoch 397/600
(train_model pid=87597) Epoch 257/600
(train_model pid=87755) Epoch 167/600
(train_model pid=87894) Epoch 55/600
(train_model pid=87279) Epoch 468/600
(train_model pid=87446) Epoch 398/600
(train_model pid=

In [6]:
# Get and print the best combinations of the HPs
best_hps = results.get_best_result().config
for hp in best_hps:
    print(f"{hp}: {best_hps.get(hp)}")

    # Stop printing if the max number of layers is lower than
    # the current layer for the number of weights 
    if hp[-1].isdigit() and int(hp[-1]) >= best_hps.get('num_layers'):
        break

epochs: 600
init_lr: 0.001
reduct_steps_lr: 1756
reduct_rate_lr: 0.82
l2_penalty: 0.086
num_layers: 2
num_weights_layer_1: 38
num_weights_layer_2: 47


## Hyperband (HB)

**Hyperband** operates on the principles of adaptive resource allocation and successive halving. 
It combines random search with a bandit-based approach to dynamically allocate more resources to promising configurations while quickly discarding less promising ones. This method allows **HB** to _explore_ a wide range of hyperparameter configurations while ensuring that only the most promising ones receive sufficient evaluation time.


The process begins by randomly sampling a set of hyperparameter configurations and **evaluating them on a small subset of resources** (e.g., a limited number of training epochs). Based on the performance of these configurations, **HB** then selects the best-performing ones (typically by taking the better half) and allocates more resources to them in subsequent iterations (e.g. continuing the training with an increased subset of epochs). Each split (subset) of the training resources is called a **"Bracket"**.
This _iterative process_ continues, progressively refining the search until only the best-performing configuration remains.


One of the key advantages of **Hyperband** is – similarly to **BO** - its ability to handle large search spaces efficiently, making it suitable for high-dimensional hyperparameter optimization tasks.
As this method runs many more trials in parallel and the overhead is significantly smaller, it is important that the evaluation is not _costly_. 
Given enough resources and the maximum epochs set to a value that guarantees convergence, **HB** can actually be run in _parallel to the actual training_ of the final model **without adding any training time**.


However, **HB** is limited by the initial random sampling. This results in randomness in the final configurations, as well as the unlikelihood of actually finding the optimal configuration.


For more information, refer to the original paper [here](https://arxiv.org/abs/1603.06560).

The implementation of **Hyperband** in Ray Tune is facilitated through the built-in **HyperBandScheduler**. This scheduler is integrated into the Ray Tune training loop, where it manages the execution of trials in parallel.

It's important to note that the **HyperBandScheduler** in Ray Tune does **NOT** strictly adhere to the _theoretical implementation_ of **Hyperband**. Instead, it operates using **groups of trials**. The total number of planned configurations is divided into several groups, with the size of each group depending on the available hardware capabilities. **Hyperband** is then executed on these groups _individually_. Finally, the performance of the best trials from each group is compared, and the overall best configuration is returned.

In [7]:
# Defining the tuner as Hyperband based on included scheduler

# definition of scheduler
hyperband = HyperBandScheduler(
    time_attr="training_iteration",  # the attribute to track progress (iterations = epochs)
    max_t=600,                       # max epochs per trial, does NOT overwrite epochs parameter in search space if that is set via build-in trainer
    reduction_factor=4               # keep only 1 in reduction_factor trials running
)
# get absolute output path
output_dir = os.path.abspath("./data/HPO_results")

# definition of the tuner
tuner_HB = tune.Tuner(
    trainable=train_model,
    param_space=search_space,
    tune_config=tune.TuneConfig(
        metric="loss",             # which metric optimize
        mode="min",                # minimize or maximize the metric
        scheduler=hyperband,       # use hyperand for optimization
        num_samples=50             # number of trials running in parallel
    ),
    run_config=tune.RunConfig(
        storage_path=output_dir, name="HB",
        verbose=1
    )
)

# activate the tuning process
results = tuner_HB.fit()

2025-06-15 21:31:02,565	INFO tune.py:1009 -- Wrote the latest version of all result files and experiment state to '/Users/erkel/Library/Mobile Documents/com~apple~CloudDocs/Uni/Arbeit Martin/PiNN-Testbench/data/HPO_results/HB' in 0.0422s.
2025-06-15 21:31:02,597	INFO tune.py:1041 -- Total run time: 947.34 seconds (947.24 seconds for the tuning loop).


In [8]:
# Get and print the best combinations of the HPs
best_hps = results.get_best_result().config
for hp in best_hps:
    print(f"{hp}: {best_hps.get(hp)}")

    # Stop printing if the max number of layers is lower than
    # the current layer for the number of weights 
    if hp[-1].isdigit() and int(hp[-1]) >= best_hps.get('num_layers'):
        break

epochs: 600
init_lr: 0.004
reduct_steps_lr: 1195
reduct_rate_lr: 0.86
l2_penalty: 0.148
num_layers: 8
num_weights_layer_1: 15
num_weights_layer_2: 15
num_weights_layer_3: 23
num_weights_layer_4: 41
num_weights_layer_5: 46
num_weights_layer_6: 44
num_weights_layer_7: 40
num_weights_layer_8: 45


## Bayesian Optimization with Hyperband (BOHB)

**BOHB**, or **Bayesian Optimization with Hyperband**, is a powerful optimization algorithm that combines the strengths of **Bayesian Optimization (BO)** and **Hyperband (HB)**. While **HB** excels at dynamically allocating resources to configurations through a successive halving strategy, **BO** is effective at exploring the hyperparameter space. **BOHB** integrates these strengths, allowing for efficient exploration and exploitation of _promising_ configurations. It retains the convergence guarantees of **BO** while being less sensitive to its own hyperparameters.


This method combines the two optimization processes by using **Bayesian optimization** to guide the search for hyperparameters while employing **Hyperband's** resource allocation strategy to efficiently explore the hyperparameter space. 
Specifically, it uses **BO** to predict a certain number of configurations and then extends these configurations randomly until the bracket of **HB** is filled. Following this, these points are analyzed using **HB**, and the resulting evaluations (including those from configurations that were stopped early) are used to refine the **BO** surrogate model. This iterative process results in more learning data for the surrogate model within the same amount of time, improving convergence speed and robustness.


**BOHB** is designed to be resource-efficient, allowing it to find optimal hyperparameters faster than traditional methods. However, while **BOHB** is efficient, the utilization of **BO** introduces _computational overhead_, which can be problematic, especially for smaller datasets or simpler models.

More information about **BHOB** again the original paper [here](https://arxiv.org/abs/1807.01774).

**BOHB** can be _simulated_ in Ray Tune by using both a HyperbandScheduler and a **BO** search algorithm, such as the one provided by Optuna.
Alternatively, it can also be implemented using the original implementation based on the **hpbandster** package. For this to work, the **BOHB search algorithm** and the **HyperbandScheduler** specifically designed for BOHB must be selected.


It is important to note that this implementation has a peculiarity: the number of iterations that the **BO** & **HB** are supposed to be repeated CANNOT be set directly. 
Instead, the parameter *num_samples* only adjusts the number of unique hyperparameter configurations. If the combined results of the **BO** predictions and the **HB** extensions yield enough trials, the algorithm will terminate early. Therefore, it is crucial to set the *num_samples* parameter **sufficiently high** to ensure proper exploration of the hyperparameter space, which is essential for finding optimal configurations, especially in complex models.

In [9]:
# Defining the tuner as BHOB based on hpbandster

# definition of the BO search algo
algo = TuneBOHB()

# definition of the HB scheduler
schedule = HyperBandForBOHB(
    time_attr="training_iteration",     # the attribute to track progress (iterations = epochs)
    max_t=600,                          # max epochs per trial, does NOT overwrite epochs parameter in search space if that is set via build-in trainer
    reduction_factor=4,                 # keep only 1 in reduction_factor trials running
    stop_last_trials=False,             # terminat all trails if they have reached max_t
)
# get absolute output path
output_dir = os.path.abspath("./data/HPO_results")

# definition of the tuner
tuner_BOHB = tune.Tuner(
    trainable=train_model,
    param_space=search_space,
    tune_config=tune.TuneConfig(
        metric="loss",             # which metric to look at
        mode="min",                # minimize or maximize the metric
        scheduler=schedule,        # set HB as scheduler
        search_alg=algo,           # set BO as search algo
        num_samples=50             # number of total unique trials evaluated
    ),
    run_config=tune.RunConfig(
        storage_path=output_dir, name="BOHB",
        verbose=1
    )
)

# start HPO
results = tuner_BOHB.fit()

2025-06-15 21:48:28,947	INFO tune.py:1009 -- Wrote the latest version of all result files and experiment state to '/Users/erkel/Library/Mobile Documents/com~apple~CloudDocs/Uni/Arbeit Martin/PiNN-Testbench/data/HPO_results/BOHB' in 0.0528s.
2025-06-15 21:48:28,978	INFO tune.py:1041 -- Total run time: 1046.13 seconds (1045.93 seconds for the tuning loop).


In [10]:
# Get and print the best combinations of the HPs
best_hps = results.get_best_result().config
for hp in best_hps:
    print(f"{hp}: {best_hps.get(hp)}")

    # Stop printing if the max number of layers is lower than
    # the current layer for the number of weights 
    if hp[-1].isdigit() and int(hp[-1]) >= best_hps.get('num_layers'):
        break

# Load the TensorBoard interactive interface for more information
# FYI: Might not show directly, just re-run this cell
# %reload_ext tensorboard
# %tensorboard --logdir ../data/HPO_results/Bayesian

epochs: 600
init_lr: 0.0047
reduct_steps_lr: 1524
reduct_rate_lr: 0.85
l2_penalty: 0.019
num_layers: 4
num_weights_layer_1: 10
num_weights_layer_2: 9
num_weights_layer_3: 18
num_weights_layer_4: 10


DO NOT USE THIS ON THE PROBLEM A HAND